**This notebook has been run on a local machine. If you do not want to run into path issues, follow the github repository for the path structure in order to eleminate those issues, or follow the instructions in this notebook.**

Github: https://github.com/OmarHory/GenderVoiceDetection

In [1]:
# NOTE: IF YOU HAVE FACED A PROBLEM IN IMPORTING, UNCOMMENT AND RUN THIS LINE BELOW, THEN REIMPORT.
#This problem is from the version of python and urllib
    

#pip uninstall parselmouth --yes

In [ ]:
#pip install praat-parselmouth

In [ ]:
#pip install SoundFile

In [1]:
import os
import librosa
import librosa.display
import random
import warnings
warnings.filterwarnings('ignore')
import re
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import missingno
from datetime import datetime
import soundfile as sf
from parselmouth.praat import run_file
import fnmatch

**IMPORTANT:**
Specify the paths

In [2]:
if 'google.colab' in str(get_ipython()):
    from google.colab import drive
    drive.mount('/content/drive/')
    print('Running on Colab.')
    
    dataPath_train = "/content/drive/My Drive/Google Colab/Data/LibriSpeech-train/train-clean-100" # Path of train speakers folders.
    root_train = "/content/drive/My Drive/Google Colab/Data/LibriSpeech-train" # Path of the Whole train dataset alongside the .txt files
    dataPath_test = "/content/drive/My Drive/Google Colab/Data/LibriSpeech-test/test-clean" # Path of train speakers folders.
    root_test = "/content/drive/My Drive/Google Colab/Data/LibriSpeech-test"  # Path of the Whole train dataset alongside the .txt files
    delimeter = '/' 
    delimeterM = '/' #A delimeter to distinguish between Local machine and Colab
    Data_file_path = '/content/drive/My Drive/Google Colab/Data'
    path_praat = '/content/drive/My Drive/Google Colab/myspsolution.praat' # Path to .praat file.
    dest_save = '/content/drive/My Drive/Google Colab/Data/NN_ML-data' # Where to save your csv and npy files.

else:
    print('Not Running on Google Colab')
    
    dataPath_train = "./Data/LibriSpeech-train/train-clean-100" # Path of train speakers folders.
    root_train = "./Data/LibriSpeech-train" # Path of the Whole train dataset alongside the .txt files
    dataPath_test = "./Data/LibriSpeech-test/test-clean" # Path of train speakers folders.
    root_test = "./Data/LibriSpeech-test"  # Path of the Whole train dataset alongside the .txt files
    delimeter = '/' 
    delimeterM = '\\' #A delimeter to distinguish between Local machine and Colab
    Data_file_path = './Data'
    path_praat = './myspsolution.praat' # Path to .praat file.
    dest_save = './Data/NN_ML-data' # Where to save your csv and npy files.

Not Running on Google Colab


In [3]:
def run_praat_file(m, p, r):
    
    """
    A fuction used to return features from the given audio file using .praat file proposed by researchers:
    Nivja DeJong and Ton Wempe, Paul Boersma and David Weenink , Carlo Gussenhoven.     
    ...

    Parameters
    ----------
    m : str
        Path to file.
    p : str
        Path to dataset folder.
    r : str
        Path with .praat file exists.
        
    Returns
    ----------
    Object
        objects outputed by the praat script
        
    """
    sound=m
    path=p
    sourcerun=r
    
    
    assert os.path.isfile(sound), "Wrong path to audio file"
    assert os.path.isfile(sourcerun), "Wrong path to praat script"
    assert os.path.isdir(path), "Wrong path to audio files"

    try:
        objects= run_file(sourcerun, -20, 2, 0.3, "yes", sound, path, 80, 400, 0.01, capture_output=True)
        z1=str( objects[1]) # This will print the info from the textgrid object, and objects[1] is a parselmouth.Data object with a TextGrid inside
        z2=z1.strip().split()
        return z2
    except:
         return -2

In [4]:
def all_features_in_audio(m, p, r):
    """
    A fuction used to return features run_praat_file(m, p, r) function.
    ...

    Parameters
    ----------
    m : str
        Path to file.
    p : str
        Path to dataset folder.
    r : str
        Path with .praat file exists.
        
    Returns
    ----------
    Object
        features: Rate of speech, Count of Syllables, Count of Pause, Speaking time, Articulation, mean frequency, 
        minimum frequency, maximum freaquency.
        
    """
    try:
        z2 = run_praat_file(m, p, r)
        return float(z2[2]), float(z2[0]), float(z2[1]), float(z2[4]), float(z2[3]), float(z2[7]), float(z2[10]), float(z2[11])
    except:
        return -1,-1,-1,-1,-1,-1,-1,-1 #To be removed later into the next step of preprocessing

In [5]:
def extract_features(sound, sample_rate, name, path, path_praat_file):
    """
    A fuction used to extract features from the given audio file using librosa: 
    Publication reference: https://dawenl.github.io/publications/McFee15-librosa.pdf
    ...

    Parameters
    ----------
    sound : numpy.ndarray
        Signal wave-form extracted from librosa.
    sample_rate : numpy.ndarray
        Sampling rate for the generated signal from librosa.
    name : str
        Name of the audio file.
    path : str
        Path of audio file's directory..
    path_praat_file : str
        Path to .praat file.
        
    Returns
    ----------
    list
        Lists of extracted features from one single audio file.
        
    """
    
    # Extract MFCCs.
    # Capture timbral/textural aspects of sound. e.g: distinguishing people in speaking.
    # Frequency Domain Feature (By FT).
    # Approximate human auditory system (Models the way which humans interpret audio).
    # The coefficients can be from 13 to 40 (I have chosen 40).
    # Calculates MFCCs on each frame.
    # outputs MFCCs with Time.
    mfccs = np.mean(librosa.feature.mfcc(y=sound, sr=sample_rate, n_mfcc=40).T, axis=0)
    
    # Short time Fourier transform to be as a given parameter in the chroma_stft feature extraction.
    # Computes several fft at different intervals.
    # Preserves time information.
    # Fixed frame size e.g: 2048 (The interval which FT will occur, then project it into the spectrogram).
    # Gives a spectrogram (time + fequency + magnitude).
    stft = np.abs(librosa.stft(sound))
    #librosa.display.specshow(librosa.amplitude_to_db(stft),sr=sample_rate)

    # Chromagram or intensity spectrogram.
    # A representation's pitch content within the time window is spread over the twelve different pitch classes.
    # Source: https://en.wikipedia.org/wiki/Chroma_feature
    chroma = np.mean(librosa.feature.chroma_stft(S=stft, sr=sample_rate).T,axis=0)
    

    # mel-scaled spectrogram.
    # It is a Spectrogram with the Mel Scale as its y axis.
    # Which is the result of some non-linear transformation of the frequency scale. 
    # This Mel Scale is constructed such that sounds of equal distance from each other on the Mel Scale
    # Source: https://towardsdatascience.com/getting-to-know-the-mel-spectrogram-31bca3e2d9d0
    mel = np.mean(librosa.feature.melspectrogram(sound, sr=sample_rate).T,axis=0)

    
    # Spectral Contrast considers the spectral peak, spectral valley and their difference in each sub-band.
    # Source: http://citeseerx.ist.psu.edu/viewdoc/download?doi=10.1.1.583.7201&rep=rep1&type=pdf
    contrast = np.mean(librosa.feature.spectral_contrast(S=stft, sr=sample_rate).T,axis=0)
    
    # With the harmonic relationship, tonnetz is a graphical representation of the tonal space.
    # To distinguish tones for an audio wave with it being a great feature for Gender Classification.
    tonnetz = np.mean(librosa.feature.tonnetz(y=librosa.effects.harmonic(sound),sr=sample_rate).T, axis=0)
    #librosa.display.specshow(tonnetz,sr=sample_rate)
    
    #Retreive all features for an audio file.
    rate_speech, syllables, pauses, time_of_speaking, articulation_rate, freq_mean, freq_min, freq_max = all_features_in_audio(path, name, path_praat_file)
    
    
    return mfccs, chroma, mel, contrast, tonnetz, rate_speech, syllables, pauses, time_of_speaking, articulation_rate, freq_mean, freq_min, freq_max

In [6]:
def dataset_creation(dataPath, root , dest_save, path_praat_file, fileFormat=".flac", delimeter= '/', delimeterM = '\\'):
    """
    A function that crawls in the given file path to all audio file then extract features from them to create a labeled dataset
    with the extracted features and labels for Gender Classification.

    ...

    Parameters
    ----------
    dataPath : str
        The path where the dataset belongs.
    root : str
        The path of the dataset alongside the .txt files.
    dest_save : str
        Destination save the .csv dataset and .npy features.
    path_praat_file : str
        Path to .praat file.
    fileFormat : str
        Audio file format.
    delimeter : str.
        To be used for splitting and concatenating paths.
    delimeterM : str
        A delimeter to distinguish between Local machine and Google Colab.
        
    Returns
    -------
    pandas.DataFrame
        The whole generated Dataset.
        
    """
    
    #Initial Dataframe for the final generated dataset.
    df = pd.DataFrame(columns=['id_speaker', 'mfccs','chroma','mel','contrast','tonnetz', 'duration', 
                               'rate_speech', 'syllables', 'pauses', 'speaking', 'artic', 'freq_mean', 
                                'freq_min', 'freq_max'])
    
    
    # loading the features using extract_features function.
    i = 0
    for path, subdirs, files in os.walk(dataPath):
        for name in files:
            #Retreive the speaker_id from the path.
            speaker_id = path.split(delimeterM)[-2].split(delimeter)[0]
            if name.endswith(fileFormat):
                #Retreive the signal and the default sample_rate from librosa.
                path_file = os.path.join(path, name)
                sound, sample_rate = librosa.load(path_file, res_type='kaiser_fast')
                f = sf.SoundFile(path_file) #Get sound properties.
                #Features are returned via extract_features.
                mfccs, chroma, mel, contrast, tonnetz, rate_speech, syllables, pauses, time_of_speaking, articulation_rate, freq_mean, freq_min, freq_max = extract_features(sound, sample_rate, path, path_file, path_praat_file)
                #Add them to the dataframe.
                df.loc[i,'id_speaker'] = speaker_id
                df.loc[i,'mfccs'] = mfccs
                df.loc[i,'chroma'] = chroma
                df.loc[i,'mel'] = mel
                df.loc[i,'contrast'] = contrast
                df.loc[i,'tonnetz'] = tonnetz
                df.loc[i,'duration'] = len(f) / f.samplerate
                df.loc[i,'rate_speech'] = rate_speech
                df.loc[i,'syllables'] = syllables
                df.loc[i,'pauses'] = pauses
                df.loc[i,'speaking'] = time_of_speaking
                df.loc[i,'artic'] = articulation_rate
                df.loc[i,'freq_mean'] = freq_mean
                df.loc[i,'freq_min'] = freq_min
                df.loc[i,'freq_max'] = freq_max
                i += 1     
    print("##########################################################")
    print('Finished Extracting Features, Now adding labels.')

    # Parsing the labels from SPEAKERS.txt file.
    labels = pd.DataFrame(columns=['id_speaker', 'gender'])
    f = open(root + delimeter + "SPEAKERS.TXT", "r", encoding="UTF8").readlines()
    i = 0
    for idx, line in enumerate(f):
        if idx > 11: # Get rid of the unneeded sentences in the beginning for the parsing.
            parsed = re.split('\s+',line)
            if parsed[4] == dataPath.split(delimeter)[-1]: # To ensure taking the right speakers from the right train/test set.
                labels.loc[i] = parsed[0], parsed[2] # Labels
                i += 1
                
    dataset = pd.merge(df, labels, on='id_speaker')  # Joining both dataframes.
    
    dataset["gender"].replace({"M": 1, "F": 0}, inplace=True) #Replacing M to 1 and F to 0.
    dataset.to_csv(dest_save + delimeter + dataPath.split(delimeter)[-1] +'.csv',index = False) # The dataset can be found in current-directory.
                                                          # This is for future purposes in case I want to improve on this notebook
    
    print('Finished Adding Labels.')
    
    
    return dataset

# Further steps:

- Generate both training-set and test-set
- Assign 'dataset_train' and 'dataset_test' to another DataFrame.
- Drop 'id_speaker' as we won't need it for modeling.
- Convert the feature Dataframe to a numpy array.
- Save it as .npy.


In [7]:
print("Generating Training-set... ")
dataset_train = dataset_creation(dataPath_train, root_train, dest_save, path_praat, delimeterM = delimeterM)

Generating Training-set... 
[]
['58', '2', '4', '5', '11.5', '14.1', '0.8', '212.69', '38.81', '206.9', '80', '376', '194', '230', '1']
0
[]
['66', '3', '4', '5', '14', '15.9', '0.9', '198.89', '39.86', '199.7', '72', '322', '178', '217', '1']
1
[]
['64', '3', '5', '5', '12.4', '13.9', '0.9', '204.35', '35.59', '199.9', '80', '323', '181', '223', '1']
2
[]
['61', '4', '4', '5', '11.6', '14.7', '0.8', '208.17', '38.56', '199.8', '80', '315', '185', '226', '0.95']
3
[]
['54', '3', '4', '5', '10.7', '12.5', '0.9', '213.86', '38.89', '207.1', '80', '355', '189', '232', '1']
4
[]
['59', '3', '4', '4', '13.3', '15.2', '0.9', '213.72', '41.79', '209.4', '80', '337', '186', '236', '1']
5
[]
['39', '1', '4', '5', '8.5', '9.6', '0.9', '204.04', '34.7', '197', '142', '391', '179', '220', '1']
6
[]
['62', '4', '4', '5', '12.4', '15', '0.8', '208.89', '36.36', '205.7', '137', '389', '186', '227', '0.95']
7
[]
['60', '4', '4', '4', '13.5', '15.4', '0.9', '189.71', '36.03', '190.9', '73', '266', '172

[]
['61', '6', '4', '5', '11.6', '14.7', '0.8', '222.91', '38.77', '212.2', '154', '367', '199', '241', '1']
74
[]
['57', '8', '4', '5', '11.3', '15.9', '0.7', '210.01', '37.46', '205.1', '82', '373', '187', '223', '1']
75
[]
['35', '5', '4', '6', '5.9', '9.4', '0.6', '225.73', '42.7', '223.4', '85', '415', '195', '254', '1']
76
[]
['14', '0', '5', '5', '2.7', '3', '0.9', '251.42', '62.02', '257', '92', '395', '197', '297', '0.95']
77
[]
['37', '3', '4', '5', '8.2', '9.7', '0.8', '231.81', '34.53', '224.9', '172', '389', '205', '255', '1']
78
[]
['63', '5', '4', '6', '11.4', '15.2', '0.8', '197.93', '44.07', '197.2', '80', '340', '181', '220', '1']
79
[]
['52', '11', '3', '5', '10.4', '16.4', '0.6', '198.94', '48.94', '195', '73', '382', '175', '221', '0.9']
80
[]
['68', '6', '4', '6', '12.3', '16.7', '0.7', '237.39', '46.55', '229', '87', '387', '197', '270', '1']
81
[]
['70', '8', '4', '6', '11', '15.9', '0.7', '227.24', '47.13', '217.1', '84', '419', '200', '252', '0.95']
82
[]
['19

[]
['9', '0', '4', '4', '2.1', '2.5', '0.9', '131.72', '46.03', '124.8', '84', '365', '100', '146', '0.95']
148
[]
['46', '4', '4', '5', '9.1', '12.9', '0.7', '131.99', '26.77', '128.1', '91', '394', '116', '147', '0.95']
149
[]
['43', '2', '4', '5', '8.2', '10.5', '0.8', '134.73', '34.54', '128.4', '81', '394', '116', '143', '0.95']
150
[]
['49', '5', '3', '5', '10.8', '17.2', '0.6', '121.35', '24.52', '117', '86', '384', '105', '133', '0.8']
151
[]
['35', '5', '2', '5', '7.2', '14', '0.5', '132.61', '47.19', '118.4', '80', '391', '96', '163', '0.8']
152
[]
['38', '5', '3', '5', '8.2', '15', '0.5', '136.81', '40.42', '129', '83', '305', '109', '160', '0.8']
153
[]
['51', '5', '4', '5', '9.8', '14.5', '0.7', '119.25', '28.64', '114.3', '80', '389', '99', '132', '0.95']
154
[]
['56', '5', '4', '5', '11.2', '15.6', '0.7', '121.11', '19', '119.5', '83', '179', '109', '130', '1']
155
[]
['16', '1', '3', '4', '3.7', '5.4', '0.7', '133.44', '44.99', '112.2', '91', '375', '104', '165', '0.85'

[]
['19', '0', '3', '4', '4.5', '5.5', '0.8', '139.47', '23.5', '136.2', '97', '214', '124', '152', '0.85']
222
[]
['39', '4', '3', '6', '6.8', '12.7', '0.5', '133.29', '29.07', '129.7', '90', '359', '114', '141', '0.85']
223
[]
['59', '7', '4', '6', '10.5', '16.2', '0.7', '132.08', '32.46', '123.2', '85', '390', '109', '146', '0.95']
224
[]
['26', '4', '3', '5', '4.9', '9', '0.5', '150.65', '54.71', '130.5', '92', '386', '111', '182', '0.7']
225
[]
['43', '6', '3', '6', '7.8', '14.7', '0.5', '148.35', '49.59', '135.2', '81', '382', '111', '169', '0.85']
226
[]
['38', '7', '3', '6', '6.6', '15', '0.4', '165.46', '58.79', '151.9', '97', '397', '122', '184', '0.7']
227
[]
['27', '3', '3', '5', '4.9', '8.6', '0.6', '131.74', '24.73', '129.8', '88', '185', '111', '152', '0.85']
228
[]
['48', '5', '3', '6', '8.7', '15.1', '0.6', '134.66', '34.93', '126.9', '79', '392', '113', '148', '0.85']
229
[]
['40', '7', '3', '5', '8.3', '15.8', '0.5', '149.36', '53.43', '127.9', '74', '400', '109', '1

[]
['57', '3', '4', '4', '12.8', '16.2', '0.8', '212.46', '59.11', '206.4', '75', '371', '168', '257', '0.95']
295
[]
['39', '1', '4', '5', '8.4', '9.5', '0.9', '184.17', '50.48', '179.8', '75', '320', '159', '217', '0.95']
296
[]
['47', '5', '3', '4', '11.2', '15.3', '0.7', '209.65', '54.69', '193.9', '71', '392', '171', '240', '0.85']
297
[]
['39', '4', '3', '4', '9.1', '13.3', '0.7', '185.44', '45.74', '182.2', '81', '335', '159', '208', '0.85']
298
[]
['56', '2', '4', '5', '11.7', '14.7', '0.8', '187.87', '44.74', '183.6', '80', '398', '160', '210', '0.95']
299
[]
['40', '4', '3', '4', '10.4', '15.9', '0.7', '227.98', '63.81', '213.7', '80', '423', '186', '274', '0.8']
300
[]
['49', '4', '4', '5', '10.2', '13.9', '0.7', '220.66', '55.5', '213', '82', '387', '184', '259', '0.95']
301
[]
['46', '6', '3', '5', '9.6', '15.3', '0.6', '220.31', '64.06', '206.8', '85', '396', '173', '264', '0.85']
302
[]
['54', '4', '4', '5', '10.8', '14.3', '0.8', '194.53', '44.92', '186.2', '80', '322',

...

28248
[]
['45', '4', '4', '5', '9.7', '12.4', '0.8', '234.79', '57.49', '219.2', '68', '412', '190', '287', '0.95']
28249
[]
['53', '4', '3', '5', '11.4', '15.3', '0.7', '248.96', '55.78', '245.1', '82', '395', '211', '287', '1']
28250
[]
['58', '5', '4', '5', '12', '15.8', '0.8', '235.72', '56.5', '220.6', '109', '419', '199', '269', '1']
28251
[]
['58', '5', '4', '5', '11.2', '14.5', '0.8', '227.55', '52.2', '227.8', '81', '348', '192', '262', '1']
28252
[]
['15', '0', '4', '5', '3', '3.4', '0.9', '222.19', '46.82', '213', '144', '360', '184', '256', '1']
28253
[]
['62', '3', '4', '5', '13.2', '16', '0.8', '236.02', '53.52', '232.1', '81', '418', '196', '268', '1']
28254
[]
['52', '5', '4', '5', '11', '14', '0.8', '242.9', '53.22', '240', '85', '413', '203', '279', '1']
28255
[]
['44', '3', '3', '4', '10.8', '13.1', '0.8', '224.32', '55.97', '216.6', '94', '395', '182', '254', '0.9']
28256
[]
['37', '4', '3', '4', '8.5', '11.7', '0.7', '221.66', '51.09', '208.8', '99', '403', '183', 

28320
[]
['44', '2', '4', '5', '9', '10.8', '0.8', '118.54', '19.04', '118.9', '80', '192', '105', '130', '1']
28321
[]
['54', '4', '4', '5', '10.4', '13.3', '0.8', '125.62', '24.56', '121.4', '80', '199', '106', '140', '1']
28322
[]
['52', '4', '4', '4', '11.7', '14', '0.8', '124.55', '32.38', '121', '81', '391', '108', '133', '1']
28323
[]
['57', '4', '4', '4', '13.1', '15.5', '0.8', '130.99', '23.92', '129.2', '80', '291', '113', '145', '1']
28324
[]
['35', '2', '3', '4', '8.1', '10.6', '0.8', '121.7', '28.61', '117.9', '81', '364', '102', '134', '0.9']
28325
[]
['60', '2', '4', '5', '13.2', '15.1', '0.9', '130.78', '21.84', '131.9', '80', '203', '114', '144', '0.95']
28326
[]
['56', '3', '4', '5', '11.1', '13.5', '0.8', '129.92', '22.02', '128.3', '80', '275', '115', '142', '1']
28327
[]
['57', '5', '4', '5', '11.4', '14.7', '0.8', '133.11', '26.94', '129', '80', '386', '116', '149', '0.95']
28328
[]
['53', '8', '3', '5', '11.2', '15.6', '0.7', '130.38', '22.98', '130.2', '80', '20

28393
[]
['50', '3', '3', '4', '12.1', '14.4', '0.8', '126.21', '19.36', '124.4', '82', '183', '114', '138', '1']
28394
[]
['46', '2', '4', '5', '10.1', '11.1', '0.9', '119.89', '17.95', '119.9', '80', '171', '107', '133', '1']
28395
[]
['45', '6', '3', '4', '10.7', '14', '0.8', '126.59', '24', '124.2', '71', '202', '108', '141', '0.9']
28396
[]
['61', '2', '4', '5', '13.2', '14.3', '0.9', '123.75', '24.42', '121.3', '80', '340', '109', '138', '1']
28397
[]
['45', '2', '4', '4', '10.3', '12.4', '0.8', '121.74', '28.47', '119.6', '80', '379', '103', '136', '1']
28398
[]
['51', '4', '4', '4', '11.8', '13.6', '0.9', '119.78', '22.54', '117.8', '80', '184', '104', '133', '1']
28399
[]
['64', '4', '4', '5', '13.1', '14.9', '0.9', '118.68', '21.05', '117.6', '80', '193', '103', '130', '1']
28400
[]
['49', '3', '4', '5', '10.3', '12.7', '0.8', '118.6', '20.52', '116.7', '80', '198', '103', '132', '1']
28401
[]
['56', '3', '4', '5', '11.7', '14.5', '0.8', '120.59', '23.7', '116.8', '78', '234'

28465
[]
['53', '4', '4', '5', '10.5', '15', '0.7', '122.26', '22.7', '115.8', '81', '285', '107', '134', '0.95']
28466
[]
['36', '3', '3', '5', '7.9', '11.6', '0.7', '136.96', '35.65', '130.8', '95', '394', '111', '155', '0.9']
28467
[]
['37', '1', '4', '5', '7.6', '9.1', '0.8', '128.18', '43.54', '115.8', '88', '392', '107', '137', '1']
28468
[]
['46', '3', '4', '5', '8.6', '10.9', '0.8', '125.06', '24.74', '119.7', '92', '326', '110', '135', '1']
28469
[]
['42', '3', '3', '5', '8', '12.3', '0.6', '120.64', '27.64', '114.3', '87', '376', '107', '124', '0.85']
28470
[]
['35', '2', '3', '4', '8.4', '12.3', '0.7', '124.31', '22.73', '118.9', '72', '198', '108', '134', '0.8']
28471
[]
['27', '1', '4', '6', '4.9', '7.5', '0.7', '120.3', '15.55', '115.7', '97', '168', '109', '131', '1']
28472
[]
['41', '5', '3', '5', '8.2', '14.7', '0.6', '121.41', '22.41', '115.5', '95', '283', '106', '131', '0.8']
28473
[]
['61', '3', '4', '5', '13', '16.7', '0.8', '125.04', '31.97', '115.6', '91', '398'

28537
[]
['30', '2', '4', '5', '5.6', '8.4', '0.7', '122.96', '27.19', '116.9', '91', '390', '108', '135', '1']
28538
##########################################################
Finished Extracting Features, Now adding labels.
Finished Adding Labels.


In [8]:
ds_train = dataset_train
ds_train.drop(['id_speaker'],axis=1, inplace=True)
features_train = np.array(ds_train)
np.save(dest_save + delimeter +'features_train', features_train)

In [12]:
dataset_train.shape

(28539, 15)

In [9]:
print("\nGenerating Test-set... ")
dataset_test = dataset_creation(dataPath_test, root_test, dest_save, path_praat, delimeterM = delimeterM)


Generating Test-set... 
[]
['31', '4', '3', '4', '7.5', '10.4', '0.7', '98.04', '13.7', '95.7', '80', '140', '87', '104', '0.85']
0
[]
['11', '0', '3', '5', '2.4', '3.3', '0.7', '105.96', '68.21', '87.3', '80', '387', '83', '96', '0.9']
1
[]
['24', '1', '4', '5', '5.3', '6.6', '0.8', '94.66', '11.6', '92.9', '79', '216', '87', '99', '1']
2
[]
['8', '0', '3', '4', '1.9', '2.7', '0.7', '175.88', '55.33', '168.1', '83', '358', '140', '187', '0.85']
3
[]
['15', '2', '3', '4', '4', '5.2', '0.8', '134.66', '33.74', '128', '75', '222', '107', '166', '0.8']
4
[]
['34', '2', '4', '4', '7.6', '9.6', '0.8', '101.86', '13.24', '98.2', '80', '142', '93', '110', '1']
5
[]
['33', '4', '3', '4', '7.8', '10.6', '0.7', '93.53', '8.58', '92.5', '80', '120', '87', '98', '0.85']
6
[]
['10', '0', '2', '3', '3.2', '4.3', '0.7', '98.83', '11.96', '98.4', '80', '121', '87', '109', '0.8']
7
[]
['21', '2', '3', '4', '4.8', '6.7', '0.7', '102.49', '15.62', '99.3', '79', '156', '91', '112', '0.9']
8
[]
['33', '3'

[]
['44', '6', '3', '5', '9.7', '14.7', '0.7', '103.62', '36.21', '97.7', '80', '395', '92', '106', '0.85']
76
[]
['8', '0', '3', '4', '2', '3', '0.7', '103.57', '18.12', '96.7', '80', '170', '92', '107', '0.7']
77
[]
['7', '3', '2', '3', '2.1', '4.4', '0.5', '97.68', '11.03', '94.4', '80', '161', '91', '104', '0.07']
78
[]
['52', '5', '3', '5', '11.5', '16.1', '0.7', '102.5', '28.07', '97.9', '80', '394', '91', '108', '0.85']
79
[]
['57', '6', '3', '5', '11.5', '16.6', '0.7', '99.84', '14.38', '96.6', '79', '167', '90', '106', '0.85']
80
[]
['16', '0', '3', '4', '3.7', '4.6', '0.8', '110.78', '14.27', '111.3', '79', '141', '98', '123', '0.95']
81
[]
['36', '3', '3', '4', '8.9', '11.5', '0.8', '108.14', '35.55', '100.4', '82', '400', '94', '109', '0.85']
82
[]
['37', '5', '3', '4', '9', '13.9', '0.6', '103.48', '25.59', '100.6', '83', '375', '94', '106', '0.7']
83
[]
['30', '4', '3', '4', '7', '10.3', '0.7', '102.07', '8.82', '101.3', '80', '133', '95', '108', '0.85']
84
[]
['50', '3',

[]
['8', '0', '3', '4', '2.2', '3', '0.7', '150.41', '13.66', '147.2', '123', '195', '140', '158', '0.8']
149
['A', 'noisy', 'background', 'or', 'unnatural-sounding', 'speech', 'detected.', 'No', 'result', 'try', 'again']
150
['A', 'noisy', 'background', 'or', 'unnatural-sounding', 'speech', 'detected.', 'No', 'result', 'try', 'again']
151
['A', 'noisy', 'background', 'or', 'unnatural-sounding', 'speech', 'detected.', 'No', 'result', 'try', 'again']
152
[]
['10', '0', '3', '3', '2.9', '3.5', '0.8', '171.84', '33.32', '164.2', '128', '261', '146', '179', '0.7']
153
[]
['52', '2', '4', '4', '13.1', '14.4', '0.9', '172.25', '43.59', '159.1', '80', '418', '147', '184', '1']
154
['A', 'noisy', 'background', 'or', 'unnatural-sounding', 'speech', 'detected.', 'No', 'result', 'try', 'again']
155
[]
['14', '2', '3', '5', '3', '5.1', '0.6', '185.47', '59.95', '168.6', '85', '396', '142', '212', '0.7']
156
[]
['33', '2', '3', '3', '9.4', '10.9', '0.9', '172.74', '35.17', '165.6', '115', '349', '1

[]
['42', '1', '4', '5', '9.3', '10.5', '0.9', '168.76', '30.53', '163', '82', '337', '152', '178', '1']
220
[]
['26', '1', '4', '5', '4.8', '6.3', '0.8', '166.49', '26.66', '163', '127', '263', '149', '180', '1']
221
[]
['35', '2', '4', '5', '7.1', '8.6', '0.8', '165.46', '30.05', '161', '70', '318', '147', '182', '1']
222
[]
['19', '0', '4', '6', '3.3', '4.3', '0.8', '235.46', '52.86', '228.4', '144', '335', '189', '278', '0.95']
223
[]
['17', '1', '3', '5', '3.6', '4.9', '0.7', '242.79', '49.41', '233.4', '158', '351', '207', '277', '1']
224
[]
['10', '1', '3', '4', '2.8', '3.7', '0.8', '245.73', '66.13', '260.9', '126', '398', '218', '278', '0.7']
225
[]
['17', '0', '5', '5', '3.1', '3.7', '0.8', '175.52', '46', '159', '114', '313', '146', '184', '1']
226
[]
['21', '1', '4', '5', '4.6', '5.8', '0.8', '231.31', '59.82', '247.4', '97', '341', '170', '273', '1']
227
[]
['7', '0', '3', '6', '1.2', '2.1', '0.6', '153.14', '15.71', '150.2', '125', '188', '144', '165', '0.9']
228
[]
['41'

[]
['31', '1', '4', '5', '6.5', '7.8', '0.8', '123.09', '30.05', '115.8', '80', '241', '101', '136', '1']
292
[]
['49', '2', '3', '4', '12.1', '14.1', '0.9', '121.08', '27.52', '115.9', '81', '387', '104', '133', '1']
293
[]
['56', '3', '4', '5', '11.4', '13.6', '0.8', '121.57', '30.39', '114.3', '80', '397', '102', '138', '1']
294
[]
['25', '0', '4', '5', '5.5', '6.3', '0.9', '115.1', '24.06', '109', '79', '348', '97', '129', '0.95']
295
[]
['57', '1', '5', '5', '10.8', '12.3', '0.9', '117.51', '24.49', '110.8', '82', '213', '100', '127', '1']
296
[]
['14', '0', '3', '4', '3.9', '4.4', '0.9', '107.13', '14.07', '105.2', '82', '142', '96', '117', '0.85']
297
[]
['21', '0', '4', '4', '4.8', '5.7', '0.8', '106.95', '14.25', '104.7', '80', '171', '99', '113', '0.95']
298
[]
['80', '4', '4', '5', '16.3', '18.5', '0.9', '114.39', '21.17', '110.8', '80', '202', '98', '126', '1']
299
[]
['14', '0', '3', '4', '3.6', '4.2', '0.9', '118.39', '18.1', '115.9', '80', '159', '106', '133', '0.85']
30

...

[]
['16', '2', '2', '3', '4.6', '6.8', '0.7', '145.47', '23.97', '141.7', '99', '218', '127', '165', '0.8']
2304
[]
['17', '1', '3', '4', '4.2', '6.2', '0.7', '140.26', '32.28', '133.3', '96', '395', '123', '151', '0.7']
2305
[]
['38', '5', '3', '4', '9.4', '13.4', '0.7', '150.24', '34.1', '148', '88', '400', '125', '170', '0.7']
2306
[]
['11', '1', '2', '3', '3.5', '4.8', '0.7', '156.12', '46.17', '149.3', '92', '373', '130', '168', '0.6']
2307
[]
['47', '4', '3', '4', '10.7', '14.6', '0.7', '153.16', '45.73', '143.7', '89', '397', '125', '169', '0.85']
2308
[]
['72', '8', '3', '5', '15.7', '22.4', '0.7', '141.09', '34.81', '133.5', '98', '381', '120', '153', '0.9']
2309
[]
['56', '6', '3', '4', '13.2', '18.7', '0.7', '151.03', '45.14', '141.7', '94', '416', '126', '162', '0.9']
2310
[]
['14', '2', '3', '4', '3.4', '5.4', '0.6', '153.74', '41.22', '144.4', '98', '375', '131', '169', '0.7']
2311
[]
['36', '0', '4', '4', '8.1', '8.8', '0.9', '105.17', '15.67', '100.9', '81', '154', '93'

[]
['9', '0', '3', '4', '2.2', '2.7', '0.8', '106.88', '14.24', '106.7', '82', '138', '95', '116', '0.85']
2377
[]
['57', '4', '3', '5', '12.3', '16.4', '0.8', '118.4', '34.77', '110.7', '80', '398', '93', '137', '1']
2378
[]
['16', '1', '3', '5', '3.3', '4.7', '0.7', '117.42', '21.37', '110.5', '80', '182', '104', '132', '0.85']
2379
[]
['19', '2', '3', '4', '4.5', '7.6', '0.6', '123.88', '34.01', '114.9', '80', '371', '99', '138', '0.7']
2380
[]
['12', '0', '3', '5', '2.5', '3.6', '0.7', '125.31', '35.09', '113.1', '82', '228', '99', '142', '0.9']
2381
[]
['9', '0', '3', '4', '2.2', '3', '0.7', '120.47', '24.52', '119.1', '84', '188', '100', '134', '0.9']
2382
[]
['36', '5', '3', '4', '8.5', '12.6', '0.7', '123.39', '30.21', '117.8', '80', '289', '102', '137', '0.7']
2383
[]
['22', '2', '3', '5', '4.8', '7.7', '0.6', '119.87', '27.72', '112.1', '82', '217', '101', '133', '0.7']
2384
[]
['8', '1', '3', '6', '1.3', '3.1', '0.4', '136.92', '69.96', '111.4', '82', '393', '100', '154', '0

[]
['74', '4', '4', '4', '16.8', '20', '0.8', '184.98', '46.5', '181.7', '81', '366', '154', '219', '0.95']
2451
[]
['13', '0', '3', '3', '3.7', '4.6', '0.8', '172.56', '40.36', '168.8', '81', '252', '153', '205', '0.8']
2452
[]
['3', '1', '1', '2', '1.5', '2.2', '0.7', '182.99', '38.64', '196.6', '85', '235', '158', '214', '0.07']
2453
[]
['23', '0', '4', '4', '5.4', '6', '0.9', '164.28', '33.64', '157.8', '80', '362', '141', '187', '1']
2454
[]
['69', '4', '4', '5', '14.7', '17.6', '0.8', '180.67', '40.66', '175.3', '80', '331', '155', '201', '1']
2455
[]
['6', '0', '2', '4', '1.3', '2.4', '0.6', '182.73', '32.79', '173.3', '117', '246', '159', '218', '0.8']
2456
[]
['8', '0', '2', '4', '2.1', '3.3', '0.7', '155.48', '35.09', '165', '79', '214', '129', '176', '0.7']
2457
[]
['13', '1', '3', '4', '3.1', '4.5', '0.7', '162.25', '44.36', '166.7', '81', '317', '128', '175', '0.85']
2458
[]
['6', '0', '3', '3', '2', '2.4', '0.8', '165.79', '34.5', '167.5', '92', '225', '150', '190', '0.8'

[]
['13', '0', '4', '4', '3.2', '3.6', '0.9', '213.91', '54.1', '191.5', '82', '338', '184', '244', '0.95']
2523
[]
['25', '1', '3', '4', '6.1', '7.2', '0.9', '214.67', '52.65', '203.1', '79', '422', '190', '232', '0.95']
2524
[]
['15', '2', '3', '6', '2.3', '4.6', '0.5', '220.13', '80.28', '198.2', '78', '414', '180', '271', '0.9']
2525
[]
['49', '0', '4', '5', '10.9', '12', '0.9', '199.09', '35.46', '191.1', '81', '356', '181', '214', '1']
2526
[]
['36', '1', '4', '5', '7.2', '8.6', '0.8', '196.7', '32.59', '195.6', '80', '274', '188', '206', '1']
2527
[]
['45', '5', '4', '5', '8.3', '11.1', '0.7', '200.98', '24.52', '198.3', '90', '270', '183', '216', '0.95']
2528
[]
['38', '1', '4', '5', '7.8', '8.9', '0.9', '204.08', '40.71', '188.4', '94', '371', '179', '210', '1']
2529
[]
['49', '4', '4', '5', '10.7', '13.9', '0.8', '217.82', '50.77', '213.2', '82', '368', '191', '252', '0.95']
2530
[]
['8', '0', '3', '4', '2.2', '2.6', '0.9', '217.43', '36.83', '219', '164', '316', '186', '236'

[]
['16', '1', '3', '5', '3.4', '4.8', '0.7', '120.45', '54.14', '105.3', '80', '399', '94', '125', '0.9']
2596
[]
['23', '2', '4', '5', '5', '6.6', '0.8', '113.27', '27.35', '108.4', '80', '255', '97', '122', '1']
2597
[]
['43', '8', '3', '5', '9.5', '14.8', '0.6', '121.46', '32.76', '112.8', '80', '319', '104', '127', '0.9']
2598
[]
['7', '1', '2', '3', '2.6', '4.5', '0.6', '101.09', '36.03', '93.2', '80', '305', '87', '103', '0.07']
2599
[]
['17', '3', '3', '6', '2.9', '5.9', '0.5', '117.5', '20.83', '115.4', '80', '186', '101', '133', '0.7']
2600
[]
['16', '4', '3', '5', '3.4', '5.8', '0.6', '119.85', '27.31', '115.7', '69', '268', '104', '130', '0.8']
2601
[]
['28', '4', '3', '4', '6.5', '10', '0.6', '124.61', '27.59', '119.3', '77', '305', '111', '131', '0.8']
2602
[]
['23', '1', '3', '4', '5.9', '7.7', '0.8', '106.96', '25.38', '101.8', '80', '241', '94', '112', '0.9']
2603
[]
['4', '1', '2', '4', '1', '2.5', '0.4', '96.51', '22.64', '88.7', '73', '167', '85', '92', '0.07']
2604

In [13]:
dataset_test.shape

(2620, 15)

In [10]:
ds_test = dataset_test
ds_test.drop('id_speaker',axis=1, inplace=True)
features_test = np.array(ds_test)
np.save(dest_save + delimeter +'features_test', features_test)

In [14]:
print('Train-set:', dataset_train.shape, '|||', 'Test-set:', dataset_test.shape)

Train-set: (28539, 15) ||| Test-set: (2620, 15)


In [15]:
def removeFilesByMatchingPattern(dirPath, pattern):
    '''
    Generic function to delete all the files from a given directory based on matching pattern.
    ...

    Parameters
    ----------
    dirPath : str
        Directory to crawl recursively at.
    pattern : str
        Regular expression that defins the files to be deleted.
        
    Returns
    -------
    list
        List of files with Error.
        
    '''
    listOfFilesWithError = []
    for parentDir, dirnames, filenames in os.walk(dirPath):
        for filename in fnmatch.filter(filenames, pattern):
            try:
                os.remove(os.path.join(parentDir, filename))
            except:
                print("Error while deleting file : ", os.path.join(parentDir, filename))
                listOfFilesWithError.append(os.path.join(parentDir, filename))
    return listOfFilesWithError

In [16]:
# Remove all Text.Grid files that were added in order to retreive the features, we do not need them anymore.

removeFilesByMatchingPattern(Data_file_path,'*.TextGrid')

[]

In [ ]:
#_features_train = np.load(dest_save + delimeter + 'features_train.npy', allow_pickle=True)
#_features_test = np.load(dest_save + delimeter + 'features_test.npy', allow_pickle=True)